In [2]:
import pandas as pd
import plotly.graph_objs as go
import plotly.express as px

df_prov_timeseries = pd.read_csv('static/csv/be-covid-provinces.csv')

In [3]:
idx = pd.date_range(df_prov_timeseries.DATE.min(), df_prov_timeseries.DATE.max())
# bar plot with bars per age groups
bars_age_groups = []
age_groups = sorted(df_prov_timeseries.AGEGROUP.unique())
for idx2, ag in enumerate(age_groups):
    df_ag = df_prov_timeseries.loc[df_prov_timeseries['AGEGROUP'] == ag]
    df_ag = df_ag.groupby(['DATE']).agg({'CASES': 'sum'})
    df_ag.index = pd.DatetimeIndex(df_ag.index)
    df_ag = df_ag.reindex(idx, fill_value=0)
    bars_age_groups.append(go.Bar(
        x=df_ag.index,
        y=df_ag['CASES'],
        name=ag,
        marker_color=px.colors.qualitative.G10[idx2]
    ))
fig_age_groups_cases = go.Figure(data=bars_age_groups)
fig_age_groups_cases.update_layout(template="plotly_white", height=500, barmode="stack", margin=dict(l=0, r=0, t=30, b=0), title="Cases per day per age group")
fig_age_groups_cases.show()

In [7]:
df_prov_timeseries.groupby(['REGION', 'AGEGROUP']).agg({'CASES': 'sum'})

CASES
REGION   AGEGROUP       
Brussels 0-9          25
         10-19        19
         20-29       184
         30-39       292
         40-49       335
         50-59       395
         60-69       299
         70-79       341
         80-89       299
         90+         139
Flanders 0-9          61
         10-19       124
         20-29      1024
         30-39      1159
         40-49      1733
         50-59      2306
         60-69      1587
         70-79      1576
         80-89      1956
         90+         702
Wallonia 0-9          42
         10-19        51
         20-29       467
         30-39       755
         40-49       972
         50-59       990
         60-69       792
         70-79       713
         80-89       745
         90+         250

In [58]:
df_prov_timeseries.AGEGROUP.unique()

array(['10-19', '20-29', '30-39', '40-49', '50-59', '70-79', '60-69',
       '0-9', '90+', '80-89'], dtype=object)

In [72]:

#c.loc[c['REGION'] == "Wallonia"]
c['CASES']['Brussels'].values

array([ 25,  19, 184, 292, 335, 395, 299, 341, 299, 139])

In [112]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

region_age = df_prov_timeseries.groupby(['REGION', 'AGEGROUP']).agg({'CASES': 'sum'})
total_age = df_prov_timeseries.groupby(['AGEGROUP']).agg({'CASES': 'sum'})

labels = sorted(df_prov_timeseries.AGEGROUP.unique())

fig = make_subplots(rows=2, cols=2, 
                    specs=[[{'type':'domain'}, {'type':'domain'}], [{'type':'domain'}, {'type':'domain'}]],
                    subplot_titles=['Wallonia', 'Flanders',"Brussels", "Belgium"],
                    horizontal_spacing=0.01, vertical_spacing=0.2)
fig.add_trace(go.Pie(labels=labels, values=c['CASES']['Wallonia'].values, name="Wallonia", sort=False, textposition="inside"),
              1, 1)
fig.add_trace(go.Pie(labels=labels, values=c['CASES']['Flanders'].values, name="Flanders", sort=False, textposition="inside"),
              1, 2)
fig.add_trace(go.Pie(labels=labels, values=c['CASES']['Brussels'].values, name="Brussels", sort=False, textposition="inside"),
              2, 1)
fig.add_trace(go.Pie(labels=labels, values=total_age['CASES'], name="Total", sort=False, textposition="inside"),
              2, 2)


fig.update_layout(
    title_text="Cases per age group, per region",
    margin=dict(l=0, r=0, t=60, b=0)
)
fig.show()

In [33]:
import json
import plotly.express as px
import pandas as pd
import plotly.graph_objs as go
import numpy as np

df_communes_tot = pd.read_csv("static/csv/be-covid-totcases.csv", dtype={"NIS5": str})
df_communes_timeseries = pd.read_csv('static/csv/be-covid-timeseries.csv')
with open('static/json/communes/be-geojson.json') as json_file:
    geojson_communes = json.load(json_file)
df_communes_tot['colorbase'] = df_communes_tot.apply(lambda row: np.log2(row.CASES) if row.CASES != 0 else 0, axis=1)
df_communes_tot['name'] = df_communes_tot.apply(lambda row: (row.FR if row.FR == row.NL else f"{row.FR}/{row.NL}").replace("_", " "), axis=1)

map_communes = px.choropleth_mapbox(df_communes_tot, geojson=geojson_communes,
                                    locations="NIS5",
                                    color='colorbase', color_continuous_scale="deep",
                                    range_color=(3, 10),
                                    featureidkey="properties.AdMuKey",
                                    center={"lat": 50.641111, "lon": 4.668889},
                                    hover_name="CASES",
                                    hover_data=["name", "CASES"],
                                    height=500,
                                    mapbox_style="carto-positron", zoom=6)
map_communes.update_geos(fitbounds="locations")
NB_TICKS = 12
map_communes.layout.coloraxis.colorbar=dict(
    title="Number of cases",
    titleside="right",
    tickmode="array",
    tickvals=list(range(1, NB_TICKS+1)),
    ticktext=[str(2**i) for i in range(1, NB_TICKS+1)],
    ticks="outside"
)
map_communes.update_traces(
    hovertemplate="<b>%{customdata[0]}</b><br>%{customdata[1]} cases"
)


print(map_communes.layout)
map_communes.update_layout(
    xaxis2 = dict(
        domain = [0.0, 0.3],
        anchor = 'y2'
    ),
    yaxis2 = dict(
         showline = True,
        domain = [0.7, 1],
        anchor = 'x2'
    ),
)

map_communes.add_trace(go.Bar(x=[1, 2, 3], y=[1, 3, 2], xaxis = 'x2',
   yaxis = 'y2'))
map_communes.data[0].below="traces"
map_communes.show()


Layout({
    'coloraxis': {'cmax': 10,
                  'cmin': 3,
                  'colorbar': {'tickmode': 'array',
                               'ticks': 'outside',
                               'ticktext': [2, 4, 8, 16, 32, 64, 128, 256, 512,
                                            1024, 2048, 4096],
                               'tickvals': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
                               'title': {'side': 'right', 'text': 'Number of cases'}},
                  'colorscale': [[0.0, 'rgb(253, 253, 204)'],
                                 [0.09090909090909091, 'rgb(206, 236, 179)'],
                                 [0.18181818181818182, 'rgb(156, 219, 165)'],
                                 [0.2727272727272727, 'rgb(111, 201, 163)'],
                                 [0.36363636363636365, 'rgb(86, 177, 163)'],
                                 [0.45454545454545453, 'rgb(76, 153, 160)'],
                                 [0.5454545454545454, 'rgb(68, 130

In [10]:
x = np.arange(1,11)
y1 = np.exp(x)
y2 = np.log(x)

trace1 = go.Scatter(
   x = x,
   y = y1,
   name = 'exp'
)
trace2 = go.Scatter(
   x = x,
   y = y2,
   xaxis = 'x2',
   yaxis = 'y2',
   name = 'log'
)
data = [trace1, trace2]
layout = go.Layout(
   yaxis = dict(showline = True),
   xaxis2 = dict(
      domain = [0.0, 0.3],
      anchor = 'y2'
   ),
   yaxis2 = dict(
      showline = True,
      domain = [0.7, 1],
      anchor = 'x2'
   )
)
fig = go.Figure(data=data, layout=layout)
fig.show()